In [ ]:
import numpy as np
import gurobipy as grb
import csv
import time
import statsmodels.api as sm
from joblib import Parallel,delayed

def five_variate(n,SNR,rho):
    beta1 = np.array([1,1,1,0,1])
    beta2 = np.array([-1,-1,-1,0,-1])
    p = len(beta1)
    Sigma = np.zeros((p,p));
    for i in range(p):
        for j in range(p):
            Sigma[i,j] = rho**(abs(i-j))
    X = np.random.multivariate_normal(mean =np.zeros(p), cov = Sigma, size = n)
    noise1 = np.random.normal(0,np.sqrt(np.var(X[:int(n/2)]@beta1)/SNR), size = int(n/2)) 
    noise2 = np.random.normal(0,np.sqrt(np.var(X[:int(n/2)]@beta2)/SNR), size = int(n/2)) 
    Y1 = X[:int(n/2)]@beta1 + noise1
    Y2 = X[int(n/2):]@beta2 + noise2
    Y = np.r_[Y1,Y2]
    lam = 0.1*n
    ols = sm.OLS(Y, X)
    ols_result = ols.fit()
    bigM = 10*float(1.96*(sum(ols_result.bse)))#1000

    M = grb.Model()
    M.Params.TimeLimit = 400
    beta = M.addMVar((int(n),5), lb = -grb.GRB.INFINITY)
    z = M.addMVar(len(Y) - 1, vtype = grb.GRB.BINARY)
    sum_of_sq = sum((Y[t] - sum(X[t,j]*beta[t,j] for j in range(5)))* (Y[t] - sum(X[t,j]*beta[t,j] for j in range(5))) for t in range(len(Y)))
    for t in range(len(Y)-1):
        for j in range(5):
            M.addConstr(beta[t+1,j] - beta[t,j] <= bigM*z[t])
            M.addConstr(beta[t+1,j] - beta[t,j] >= -bigM*z[t])
    #optional constratins to add more cuts
    M.addConstr(sum(z) <= 5)
    for t in range(1, len(Y) - 2):
        M.addConstr(z[t-1] + z[t] + z[t+1] <= 1)
    M.setObjective(sum_of_sq+ lam*sum(z))
    M.optimize()
    beta_hat = [beta[t].x for t in range(len(Y))]
    z_hat = [z[t].x for t in range(len(Y)-1)]
    opt_gap = M.MIPGap
    return z_hat, opt_gap,beta_hat

SNR_list = np.array([6, 3.52, 2.07, 1.22, 0.71])
rho_list = np.array([0, 0.3, 0.7])
n_list = np.array([1000])

header = ['Repitition','Time','rho', 'SNR', 'n', 'Optimality Gap', 'Change Points']#, 'beta_hat', 'nonzero count']
f = open('simulation_five_variate.csv', 'w')
writer = csv.writer(f)
writer.writerow(header)
f.close()

def to_repeat(rep):
    for n in n_list:
        for SNR in SNR_list:
            for rho in rho_list:
                tik = time.time()
                z_hat, opt_gap, beta_hat = five_variate(n,SNR,rho)
                tok = time.time()
                duration = tok - tik
                cps = [idx for idx,item in enumerate(z_hat) if item == 1 ]
                # Write result
                resultrow = [rep,duration,rho,SNR, n, opt_gap, cps]
                f = open('simulation_five_variate.csv', 'a')
                writer = csv.writer(f)
                writer.writerow(resultrow)
                f.close()
                
Parallel(n_jobs = 8)(delayed(to_repeat)(rep) for rep in range(500)) #Tomo's machine has 8 cores.

Set parameter Username
Set parameter Username
Set parameter Username
Set parameter Username
Set parameter Username
Set parameter Username
Academic license - for non-commercial use only - expires 2024-02-18
Academic license - for non-commercial use only - expires 2024-02-18
Academic license - for non-commercial use only - expires 2024-02-18
Set parameter TimeLimit to value 400
Set parameter TimeLimit to value 400
Set parameter TimeLimit to value 400
Academic license - for non-commercial use only - expires 2024-02-18
Set parameter TimeLimit to value 400
Academic license - for non-commercial use only - expires 2024-02-18
Set parameter TimeLimit to value 400
Academic license - for non-commercial use only - expires 2024-02-18
Set parameter TimeLimit to value 400
Set parameter Username
Academic license - for non-commercial use only - expires 2024-02-18
Set parameter TimeLimit to value 400
Set parameter Username
Academic license - for non-commercial use only - expires 2024-02-18
Set parameter


Root simplex log...

Iteration    Objective       Primal Inf.    Dual Inf.      Time
    9019    2.5193383e+03   0.000000e+00   3.800226e+03      5s

Root simplex log...

Iteration    Objective       Primal Inf.    Dual Inf.      Time
    9451    2.7402277e+03   0.000000e+00   3.780708e+03      5s

Root simplex log...

Iteration    Objective       Primal Inf.    Dual Inf.      Time
    9169    2.8874130e+03   0.000000e+00   3.948592e+03      5s

Root simplex log...

Iteration    Objective       Primal Inf.    Dual Inf.      Time
    9093    2.5443278e+03   0.000000e+00   3.640022e+03      5s

Root simplex log...

Iteration    Objective       Primal Inf.    Dual Inf.      Time
    8852    2.5428473e+03   0.000000e+00   3.755919e+03      5s
   13953    2.0912819e+03   0.000000e+00   2.733270e+03     10s
   14076    2.1243999e+03   0.000000e+00   2.874486e+03     10s
   13876    2.0422951e+03   0.000000e+00   3.220009e+03     10s
   13393    2.0375314e+03   0.000000e+00   2.659985e+03   

     1     4  572.84637    1  125 4459.92554  572.84637  87.2%  22.0   55s
     0     2  651.13575    0  146 4638.32346  651.13575  86.0%     -   58s
     0     2  694.96940    0  150 4891.21066  694.96940  85.8%     -   59s
     1     4  696.35149    1  152 4891.21066  696.35149  85.8%   106   61s
    11    16  706.98158    4  155 4638.66313  706.98158  84.8%  93.0   60s
     0     2  657.59971    0  163 5194.89977  657.59971  87.3%     -   60s
     3     8  674.83783    2  150 4638.32346  674.83783  85.5%   200   61s
     7    12  572.66961    3  131 4610.64939  572.66961  87.6%   137   62s
    19    24  652.28529    6  152 4563.80004  646.83173  85.8%  79.7   62s
     0     2  558.28933    0  120 4208.53764  558.28933  86.7%     -   61s
    11    16  578.43360    4  124 4459.92554  578.43360  87.0%   155   61s
     3     8  696.54038    2  150 4891.21066  696.54038  85.8%   125   65s
    15    20  573.98543    5  128 4610.64939  573.21778  87.6%  79.5   65s
    23    28  661.90355  

   225    74  657.92146   49   73  677.04920  562.26269  17.0%  57.0  145s
    80    36  700.35327   18  117  786.26808  677.91959  13.8%   140  147s
   192    67  686.13771   31  131  767.24882  646.83173  15.7%  72.7  147s
   195    61  682.66365   55   66  686.88295  591.70609  13.9%  68.4  146s
    57    31  708.68780   15  152  798.85298  690.03900  13.6%   199  148s
    49    34  730.68581   13  160  847.96119  730.68581  13.8%   142  149s
    73    34  747.20530   19  145  838.76255  709.01978  15.5%   151  150s
    96    41  700.36455   19  106  786.26808  677.91959  13.8%   121  150s
   223    71  762.63047   34  129  767.24882  646.83173  15.7%  68.0  150s
   270    81  659.28435   58   75  677.04920  562.26269  17.0%  52.1  150s
   308   105  686.39881   50  107  690.15099  574.10052  16.8%  53.2  151s
   246    73  684.25262   73   64  686.88295  591.70609  13.9%  60.6  150s
    61    31  709.01106   16  146  798.85298  690.03900  13.6%   205  151s
    54    35  730.73605  

   801   242  643.08028  105   97  677.04920  562.88527  16.9%  38.5  222s
   478   160  786.39453   12  131  838.76255  709.61852  15.4%  54.9  225s
  1127   444  680.31660   23   95  686.88295  600.47541  12.6%  36.8  224s
  1296   575  739.25623  228  123  767.24882  648.84128  15.4%  34.8  225s
   586   237  768.74663   93  136  847.96119  731.11659  13.8%  49.6  226s
   840   306  654.81007  123   97  690.15099  574.10052  16.8%  37.3  227s
   876   243  645.38464  124   98  677.04920  562.88527  16.9%  37.4  227s
   772   253  757.22603  158  103  786.26808  677.91959  13.8%  42.8  228s
   509   174  763.81743    9  125  798.85298  691.14735  13.5%  68.6  228s
   601   262  799.03614   95  141  847.96119  731.11659  13.8%  49.6  230s
   533   181  786.50092   15  120  838.76255  709.61852  15.4%  52.2  230s
  1380   623  740.63205  253  126  767.24882  648.84128  15.4%  35.2  230s
  1200   471  685.19576   39  106  686.88295  602.85847  12.2%  36.6  229s
   906   342  656.09624  

...

   152   172 9026.96764   33  301 21509.6352 8616.65970  59.9%  62.5  340s
   105   114 2674.03906   24  335 4825.12051 2574.31660  46.6%  76.0  339s
   201   224 7857.70815   47  290 15654.1218 7491.47362  52.1%  60.3  343s
   401   441 5261.96679   88  268 8162.72732 4971.72638  39.1%  37.0  340s
   785   844 6156.48625  177  276 10286.7892 5569.27155  45.9%  32.4  343s
H  799   844                    10103.399292 5569.27155  44.9%  32.3  343s
   135   157 7783.10471   32  315 14033.5857 7545.02846  46.2%  68.7  344s
   113   123 2681.65156   26  340 4825.12051 2574.31660  46.6%  73.5  344s
   223   248 7901.08163   52  290 15654.1218 7491.47362  52.1%  58.6  349s
   440   482 5275.08688   95  273 8162.72732 4971.72638  39.1%  35.5  345s
   156   176 7796.82585   35  315 14033.5857 7545.02846  46.2%  64.7  349s
   247   275 7917.25300   58  287 15654.1218 7491.47362  52.1%  55.9  353s
H  171   186                    21474.955490 8616.65970  59.9%  59.1  350s
H  173   186             

Set parameter TimeLimit to value 400
    27    32 2207.77003    8  257 6970.71248 2202.98957  68.4%   112  204s
H   28    32                    5262.5194680 2202.98957  58.1%   108  204s
H   29    32                    3159.9208399 2202.98957  30.3%   106  204s
    31    36 2211.78856    9  257 3159.92084 2202.98957  30.3%   103  205s
    51    56 2221.58155   14  264 3159.92084 2202.98957  30.3%  78.4  211s
    65    73 2228.90191   18  267 3159.92084 2202.98957  30.3%  70.6  215s
    84    93 2235.31625   21  266 3159.92084 2202.98957  30.3%  62.2  220s
   107   117 2243.03362   26  270 3159.92084 2202.98957  30.3%  57.4  226s
   131   149 2249.59080   30  273 3159.92084 2202.98957  30.3%  53.1  230s
   187   209 2265.39810   43  277 3159.92084 2202.98957  30.3%  49.3  236s
   258   275 2285.76493   59  286 3159.92084 2202.98957  30.3%  45.0  244s
   274   294 2289.07255   62  289 3159.92084 2202.98957  30.3%  44.3  246s
   325   355 2307.14417   75  296 3159.92084 2202.98957  30.3% 

  1142  1210 2457.05236  266  293 3159.92084 2202.98957  30.3%  28.3  324s
   11826    9.9439769e+03   0.000000e+00   5.592040e+03     15s
   11988    1.0293234e+04   0.000000e+00   5.637604e+03     15s
   12573    3.5840369e+03   0.000000e+00   3.463873e+03     15s
   15556    1.8852219e+03   0.000000e+00   2.540676e+03     20s
   14832    1.9597822e+03   0.000000e+00   2.704894e+03     20s
   15150    2.0907384e+03   0.000000e+00   2.973013e+03     20s
   13932    9.3489164e+03   0.000000e+00   4.256114e+03     20s
   13932    9.8006325e+03   0.000000e+00   4.550766e+03     20s
  1209  1291 2470.11815  287  290 3159.92084 2202.98957  30.3%  28.0  331s
Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (mac64[x86])

CPU model: Intel(R) Core(TM) i5-8257U CPU @ 1.40GHz
Thread count: 4 physical cores, 8 logical processors, using up to 8 threads

Optimize a model with 10988 rows, 5999 columns and 33960 nonzeros
Model fingerprint: 0xa30f118e
Model has 15000 quadratic objective terms
Variable

     0     0 2191.22325    0  252 6798.41062 2191.22325  67.8%     -   73s
     0     0  631.60475    0  135 5032.20364  631.60475  87.4%     -   76s
   39691    5.9288906e+02   0.000000e+00   0.000000e+00     77s

Root relaxation: objective 5.928891e+02, 39691 iterations, 76.39 seconds (15.57 work units)

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Expl Unexpl |  Obj  Depth IntInf | Incumbent    BestBd   Gap | It/Node Time

     0     0  592.88906    0  123 4633.69807  592.88906  87.2%     -   76s
   26332    2.3458065e+03   0.000000e+00   7.396158e+02     55s
     0     0  568.51575    0  129 4606.27450  568.51575  87.7%     -   80s
H    0     0                    23146.407623 6930.37542  70.1%     -   77s
     0     0 7254.01232    0  294 24040.6353 7254.01232  69.8%     -   78s
     0     0  592.88906    0  123 4633.69807  592.88906  87.2%     -   80s
     0     0 6938.21280    0  285 23146.4076 6938.21280  70.0%     -   80s
  1864  2018 2589.07351  45

    23    28 7200.35749    7  293 23146.4076 7200.35749  68.9%   171  215s
    63    31  680.54130   16  110  766.13951  641.98335  16.2%   137  216s
   186    46  686.81875   56   77  687.27375  584.29038  15.0%  55.9  219s
   141    52  619.42858   23  114  714.47937  597.59075  16.4%  72.1  217s
   205    52  651.93121    4  120  687.27375  584.29038  15.0%  55.6  222s
    74    32  680.62256   17  107  766.13951  641.98335  16.2%   125  220s
   176    59  622.85400   27  110  714.47937  597.59075  16.4%  65.0  222s
   220    54  652.01688    5  110  687.27375  584.29038  15.0%  55.3  225s
   195    64  624.63143   30  109  714.47937  597.59075  16.4%  62.4  225s
    90    95 2231.75745   25  271 6151.08824 2204.06595  64.2%  52.5  223s
   101    37  680.69726   19  100  766.13951  641.98335  16.2%   100  226s
   263    76  652.47158   13  109  687.27375  584.29038  15.0%  51.3  231s
    94   104 2232.30195   26  272 6151.08824 2204.06595  64.2%  51.5  227s
    27    32 2139.39431  

In [6]:
bigM

8.833158764852824